In [1]:
# libs
import pandas as pd
from glob import glob

import altair as alt

from src.mzml_parser import df_from_mzml

In [2]:
# read in targets of interest
targets = pd.read_csv('targets.csv', sep="\t", converters = {'precursor': str, 'product': str})
targets['transition'] = targets.apply(lambda x: f"{x['precursor']}_{x['product']}_{x['polarity']}", axis=1)
targets

name precursor product   rt polarity  rt_start  rt_end       transition
0   d4_LEA     328.3    66.2  782      pos       777     787   328.3_66.2_pos
1  d4_DHEA     376.3    66.2  781      pos       776     786   376.3_66.2_pos
2   d8_AEA     356.3    62.2  783      pos       778     788   356.3_62.2_pos
3  d8_2_AG     387.3   294.2  795      pos       790     800  387.3_294.2_pos
4   d4_PEA     304.3    62.2  798      pos       793     803   304.3_62.2_pos
5   d4_OEA     330.3    66.2  805      pos       800     810   330.3_66.2_pos
6   d3_SEA     331.3    62.2  827      pos       822     832   331.3_62.2_pos
7  d8_NADA     448.4     137  796      pos       791     801    448.4_137_pos

In [3]:
# define pciis transition to use
pciis = {'name': '2F_AEA_02','transition': '350.3_269.2_pos'}

In [4]:
# read in signal data (from mzml files)
signal_df = pd.concat([df_from_mzml(mzml_file) for mzml_file in glob('mzML/*.mzML')])

In [5]:
# extract pciis signal
pciis_data = signal_df[signal_df['transition'] == pciis['transition']][['file', 'rt','intensity']].copy()

# rename column header
pciis_data['pciis'] = pciis_data['intensity']
pciis_data = pciis_data.drop(['intensity'], axis=1)

# prepare index for join with target signal using file/rt
pciis_data = pciis_data.set_index(['file', 'rt'])

dfs = []
for tIdx, target in targets.iterrows():
    
    # extract target signal
    target_data = signal_df[signal_df['transition'] == target['transition']].copy()
    
    # keep index, in case we have multiple targets with the same transition
    target_data['target'] = tIdx
       
    # prepare index for join with pciis signal using file/rt
    target_data = target_data.set_index(['file', 'rt'])    
    
    # glue the pciis signal to the dataframe as a column
    dfs.append(target_data.join(pciis_data['pciis']).reset_index())
    
df = pd.concat(dfs)
df

file       rt      transition  intensity  \
0     mzML/inj043_PlDiv2_L.mzML  760.760  328.3_66.2_pos          0   
1     mzML/inj043_PlDiv2_L.mzML  760.885  328.3_66.2_pos          0   
2     mzML/inj043_PlDiv2_L.mzML  761.010  328.3_66.2_pos          0   
3     mzML/inj043_PlDiv2_L.mzML  761.135  328.3_66.2_pos          0   
4     mzML/inj043_PlDiv2_L.mzML  761.260  328.3_66.2_pos          0   
...                         ...      ...             ...        ...   
3123  mzML/inj050_AcDiv3_H.mzML  799.510   448.4_137_pos        735   
3124  mzML/inj050_AcDiv3_H.mzML  799.635   448.4_137_pos        713   
3125  mzML/inj050_AcDiv3_H.mzML  799.760   448.4_137_pos        820   
3126  mzML/inj050_AcDiv3_H.mzML  799.885   448.4_137_pos       1034   
3127  mzML/inj050_AcDiv3_H.mzML  800.010   448.4_137_pos       1194   

               sample  target   pciis  
0     inj043_PlDiv2_L       0  249691  
1     inj043_PlDiv2_L       0  240162  
2     inj043_PlDiv2_L       0  231284  
3     inj043_PlDiv2_L       0  219764  
4     inj043_PlDiv2_L       0  204408  
...               ...     ...     ...  
3123  inj050_AcDiv3_H       7  171815  
3124  inj050_AcDiv3_H       7  175124  
3125  inj050_AcDiv3_H       7  174472  
3126  inj050_AcDiv3_H       7  171090  
3127  inj050_AcDiv3_H       7  168272  

[24979 rows x 7 columns]

In [6]:
# determine ratio
df['ratio'] = df['intensity']/df['pciis']
df

# performe some basic alignment on ratio
# TODO: 

file       rt      transition  intensity  \
0     mzML/inj043_PlDiv2_L.mzML  760.760  328.3_66.2_pos          0   
1     mzML/inj043_PlDiv2_L.mzML  760.885  328.3_66.2_pos          0   
2     mzML/inj043_PlDiv2_L.mzML  761.010  328.3_66.2_pos          0   
3     mzML/inj043_PlDiv2_L.mzML  761.135  328.3_66.2_pos          0   
4     mzML/inj043_PlDiv2_L.mzML  761.260  328.3_66.2_pos          0   
...                         ...      ...             ...        ...   
3123  mzML/inj050_AcDiv3_H.mzML  799.510   448.4_137_pos        735   
3124  mzML/inj050_AcDiv3_H.mzML  799.635   448.4_137_pos        713   
3125  mzML/inj050_AcDiv3_H.mzML  799.760   448.4_137_pos        820   
3126  mzML/inj050_AcDiv3_H.mzML  799.885   448.4_137_pos       1034   
3127  mzML/inj050_AcDiv3_H.mzML  800.010   448.4_137_pos       1194   

               sample  target   pciis     ratio  
0     inj043_PlDiv2_L       0  249691  0.000000  
1     inj043_PlDiv2_L       0  240162  0.000000  
2     inj043_PlDiv2_L       0  231284  0.000000  
3     inj043_PlDiv2_L       0  219764  0.000000  
4     inj043_PlDiv2_L       0  204408  0.000000  
...               ...     ...     ...       ...  
3123  inj050_AcDiv3_H       7  171815  0.004278  
3124  inj050_AcDiv3_H       7  175124  0.004071  
3125  inj050_AcDiv3_H       7  174472  0.004700  
3126  inj050_AcDiv3_H       7  171090  0.006044  
3127  inj050_AcDiv3_H       7  168272  0.007096  

[24979 rows x 8 columns]

In [7]:
for tIdx, target in targets.iterrows():
    
    # extract target signal
    target_data = df[df['target'] == tIdx].copy()   

    alt.Chart(target_data).mark_line().encode(
        x='rt',
        y='intensity',
        color='sample'
    ).properties(
        width=700,
        height=200
    ).display()

alt.Chart(...)

alt.Chart(...)

alt.Chart(...)

alt.Chart(...)

alt.Chart(...)

alt.Chart(...)

alt.Chart(...)

alt.Chart(...)